In [1]:
%matplotlib qt
#%matplotlib notebook 
from mpl_toolkits.mplot3d import Axes3D
from matplotlib import cm
from matplotlib.animation import FFMpegWriter

%config InlineBackend.figure_format = 'retina'
import matplotlib.pyplot as plt
import numpy as np

In [2]:
class CosmicSimulation:
    def __init__(self, planet_destroy = False, 
                 planet_melt = False, sun_merge = True, G = 6.67 * 10**(-11), 
                 merge_distance = 1, tail_length = 10):
        self.tail_length = tail_length
        self.planet_destroy = planet_destroy
        self.planet_melt = planet_melt
        self.sun_merge = sun_merge
        self.merge_distance = merge_distance
        self.G = G
        self.planets = []
        self.suns = []
        self.timestep = 0
        
        self.y = np.array([])
        self.m = np.array([])
        self.destroyed = np.array([])
        
    def record(self, title = "Default", artist = "Basiq", comment = "Comment",
               fps = 60, bitrate = 20000, time = 10, dt = 0.01,
               xlimit = 0, ylimit = 0):
        metadata = dict(title = title, artist = artist)
        writer = FFMpegWriter(fps = fps, metadata = metadata, bitrate = bitrate)
        fig = plt.figure(dpi=200)
        
        #timestep = 60*60*24*365*dt
        for i in range(len(self.planets)):
            self.y = np.append(self.y, self.planets[i].get_arr())
            self.m = np.append(self.m, self.planets[i].get_mass())
            self.destroyed = np.append(self.destroyed, self.planets[i].is_destroyed())
            #self.planets[i].arr = np.append(self.planets[i].arr[0:2], self.planets[i].arr[2:4]*timestep)
        for i in range(len(self.suns)):
            self.y = np.append(self.y, self.suns[i].get_arr())
            self.m = np.append(self.m, self.suns[i].get_mass())
            self.destroyed = np.append(self.destroyed, self.suns[i].is_destroyed())
            #self.suns[i].arr = np.append(self.suns[i].arr[0:2], self.suns[i].arr[2:4]*timestep)
        with writer.saving(fig, title +".mp4", dpi=200):
            for it in range(time):
                if (it%10==0): 
                    print(it,end='')
                else:
                    print('.',end='')
                self.timestep = it    
                self.check_contact()
                
                f1 = self.KeplerODE(it       ,self.y          )
                f2 = self.KeplerODE(it+dt/2.0,self.y+f1*dt/2.0)
                f3 = self.KeplerODE(it+dt/2.0,self.y+f2*dt/2.0)
                f4 = self.KeplerODE(it+dt    ,self.y+f3*dt    )

                self.y = self.y + (f1 + 2.0*f2 + 2.0*f3 + f4) / 6.0 * dt
                
                self.draw_scene(xlimit, ylimit)
                plt.pause(0.05)
                writer.grab_frame()
                
    def check_contact(self):
        for i in range(len(self.suns)):
            currpos = self.suns[i].get_arr()
            for j in range(len(self.suns)):
                if i!=j and not self.suns[i].is_destroyed() and not self.suns[j].is_destroyed():
                    otherpos = self.suns[j].get_arr()
                    distance = np.linalg.norm(currpos - otherpos)
                    if distance < self.merge_distance and self.sun_merge and not (self.suns[i].is_destroyed()
                                                               or self.suns[i].is_destroyed()):
                        self.sun_combine(i, j)
        
    def sun_combine(self, i, j):
        if self.suns[i].get_mass() < self.suns[j].get_mass():
            i, j = j, i
        # using equation m_1*v_1 + m_2*v_2 = (m_1 + m_2)*v_3 to get v_3 = (m_1*v_1 + m_2*v_2)/(m_1 + m_2) 
        m1, m2 = self.suns[i].get_mass(), self.suns[j].get_mass()
        v1, v2 = self.suns[i].get_arr()[2:4], self.suns[j].get_arr()[2:4]
        v3 = (m1*v1 + m2*v2)/(m1 + m2)
        self.suns[i].arr[2:4] = v3
        
        self.destroyed[j + len(self.planets)] = self.timestep
        #self.suns[i].arr[0:4] = np.array([0., 0., 0., 0.])
        self.m[i]+= m2
        self.suns[j].destroyed = True     
        for k in range(len(self.m)):
            if self.m[k]==self.m[j]:
                self.y[k*4:k*4+4] = np.array([0.,0., 0., 0.])
        print("Sun", i, "has absorbed Sun", j)
        
    def KeplerODE(self, t, y):
        newy = np.array([])
        for i in range(len(self.destroyed)):
            if self.destroyed[i]:
                newy = np.append(newy, [0, 0, 0 , 0])
                continue;
            m1 = self.m[i]
            r1 = y[i*4:i*4+2]
            dr = y[i*4+2:i*4+4]
            total_force = np.array([0.,0.])
            for j in range(len(self.destroyed)):
                if i!=j and not self.destroyed[j]:
                    m2 = self.m[j]
                    r2 = y[j*4:j*4+2]
                    curr_force = self.Force(m1, m2, r1, r2)
                    total_force += curr_force
            dv = total_force/m1
            newy = np.append(newy, [dr, dv])
        return newy

    
    def Force(self, m1, m2, r1, r2):
        G = self.G
        divider = max(np.linalg.norm(r1 - r2)**3, 0.0001)
        return -m1 * m2 * G / divider * (r1 - r2)     
    
    def draw_scene(self, xlimit, ylimit):
        plt.clf()
        if xlimit:
            plt.xlim(xlimit)
        if ylimit:
            plt.ylim(ylimit)
        num_planets = len(self.planets)
        for i in range(len(self.planets)):
            temp_pos = self.y[i*4: i*4 +2]
            self.planets[i].update_arr(temp_pos)
            plt.plot(self.planets[i].get_pastX(),self.planets[i].get_pastY(),c = self.planets[i].get_tail_color())
            plt.plot(temp_pos[0], temp_pos[1],'o',mfc='w', c = self.planets[i].get_color())
        for i in range(len(self.suns)):
            temp_pos = self.y[(i+num_planets)*4: (i+num_planets)*4 +2]
            self.suns[i].update_arr(temp_pos)
            #plt.plot(self.suns[i].get_pastX(),self.suns[i].get_pastY(),c = self.suns[i].get_tail_color())
            if not self.suns[i].is_destroyed():
                plt.plot(temp_pos[0], temp_pos[1],'*',mfc='w', c = self.suns[i].get_color())
        plt.draw()
 
    
    def addPlanet(self, mass = 1, pos = (0,0), speed = (0,0), color = "red", tail_color = "red"):
        planet = Celestial(mass = mass, pos = pos, speed = speed, color = color, tail_color = tail_color, 
                           tail_length = self.tail_length)
        self.planets.append(planet)
        
    def addSun(self, mass = 1, pos = (0,0), speed = (0,0), color = "blue", tail_color = "blue"):
        sun = Celestial(mass = mass, pos = pos, speed = speed, color = color, tail_color = tail_color, 
                        tail_length = self.tail_length)
        self.suns.append(sun) 

class Celestial:
    def __init__(self, mass, pos, speed, color, tail_color, tail_length = 10):
        self.mass = mass
        self.arr = np.array([pos[0], pos[1], speed[0], speed[1]]) # x, y, vx, vy
        self.color = color
        self.tail_color = tail_color
        self.pastX = np.array([pos[0]] * tail_length)
        self.pastY = np.array([pos[1]] * tail_length)
        self.destroyed = 0
        self.tail_length = tail_length
    
    def get_mass(self):
        return self.mass
    def get_arr(self):
        return self.arr
    def get_color(self):
        return self.color
    def get_tail_color(self):
        return self.tail_color
    def get_pastX(self):
        return self.pastX
    def get_pastY(self):
        return self.pastY
    def is_destroyed(self):
        return self.destroyed
    
    def update_arr(self, new_arr):
        if self.is_destroyed():
            self.pastX = self.pastX[1:]
            self.pastY = self.pastY[1:]
        elif len(self.pastX > self.tail_length):
            self.pastX = np.append(self.pastX[1:], [new_arr[0]])
            self.pastY = np.append(self.pastY[1:], [new_arr[1]])
        else:
            self.pastX = np.append(self.pastX, [new_arr[0]])
            self.pastY = np.append(self.pastY, [new_arr[1]])
        self.arr = new_arr
    def destroy(self):
        self.destroyed = True

In [ ]:
million_kilo = 1000000

m_mercury = 3.285 * 10**23
d_mercury = 57 * million_kilo
pos_mercury = np.array([0,-1]) * d_mercury
v_mercury = 1470000
vel_mercury = np.array([1,0]) * v_mercury

m_venus = 4.867 * 10**24
d_venus = 108 * million_kilo
pos_venus = np.array([0,-1]) * d_venus
v_venus = 1090000
vel_venus = np.array([1,0]) * v_venus

m_earth = 5.972 * 10**24
d_earth = 149 * million_kilo
pos_earth = np.array([0,-1]) * d_earth
v_earth = 940000
vel_earth = np.array([1,0]) * v_earth

m_mars = 6.39 * 10**23
d_mars = 228 * million_kilo
pos_mars = np.array([0,-1]) * d_mars
v_mars = 760000
vel_mars = np.array([1,0]) * v_mars

m_jupiter = 1.898 * 10**27
d_jupiter = 780 * million_kilo
pos_jupiter = np.array([0,-1]) * d_jupiter
v_jupiter = 407000
vel_jupiter = np.array([1,0]) * v_jupiter

m_saturn = 5.68 * 10**26
d_saturn = 1437 * million_kilo
pos_saturn = np.array([0,-1]) * d_saturn
v_saturn = 303300
vel_saturn = np.array([1,0]) * v_saturn

m_uranus = 8.68 * 10**25
d_uranus = 2871 * million_kilo
pos_uranus = np.array([0,-1]) * d_uranus
v_uranus = 213300
vel_uranus = np.array([1,0]) * v_uranus

m_neptune = 1.024* 10**26
d_neptune = 4530 * million_kilo
pos_neptune = np.array([0,-1]) * d_neptune
v_neptune = 170140
vel_neptune = np.array([1,0]) * v_neptune

m_sun = 1.989 * 10**30

e_move = np.array([-700000, 0])
cosmo = CosmicSimulation(planet_destroy = True, planet_melt = True, sun_merge = True, merge_distance = 10000,
                        tail_length = 1000)

cosmo.addSun(mass= m_sun, pos = (0,0), color = "yellow", tail_color= "yellow")
cosmo.addPlanet(mass = m_mercury,pos = pos_mercury, speed = vel_mercury + e_move, color = "orange", tail_color= "orange")
cosmo.addPlanet(mass = m_venus,pos = pos_venus, speed = vel_venus, color+ e_move = "blue", tail_color= "blue")
cosmo.addPlanet(mass = m_earth,pos = pos_earth, speed = vel_earth, color+ e_move = "green", tail_color= "green")
cosmo.addPlanet(mass = m_mars,pos = pos_mars, speed = vel_mars, color + e_move= "red", tail_color= "red")
cosmo.addPlanet(mass = m_jupiter,pos = pos_jupiter, speed = vel_jupiter+ e_move, color = "brown", tail_color= "brown")
cosmo.addPlanet(mass = m_saturn,pos = pos_saturn, speed = vel_saturn+ e_move, color = "purple", tail_color= "purple")
cosmo.addPlanet(mass = m_uranus,pos = pos_uranus, speed = vel_uranus+ e_move, color = "cyan", tail_color= "cyan")
cosmo.addPlanet(mass = m_neptune,pos = pos_neptune, speed = vel_neptune+ e_move, color = "violet", tail_color= "violet")

curr_frame = d_neptune *1.01
cosmo.record(title = "e move ",
             fps = 60, xlimit = [-curr_frame, curr_frame],ylimit = [-curr_frame, curr_frame],time = 60*30, dt = 10)

In [13]:
cosmo = CosmicSimulation(planet_destroy = True, planet_melt = True, sun_merge = True, merge_distance = 10000,
                        tail_length = 50)

cosmo.addSun(mass= m_sun, pos = (0,0), color = "yellow", tail_color= "yellow")
cosmo.addPlanet(mass = m_mercury,pos = pos_mercury, speed = vel_mercury, color = "orange", tail_color= "orange")
cosmo.addPlanet(mass = m_venus,pos = pos_venus, speed = vel_venus, color = "blue", tail_color= "blue")
cosmo.addPlanet(mass = m_earth,pos = pos_earth, speed = vel_earth, color = "green", tail_color= "green")
cosmo.addPlanet(mass = m_mars,pos = pos_mars, speed = vel_mars, color = "red", tail_color= "red")
cosmo.addPlanet(mass = m_jupiter,pos = pos_jupiter, speed = vel_jupiter, color = "brown", tail_color= "brown")
cosmo.addPlanet(mass = m_saturn,pos = pos_saturn, speed = vel_saturn, color = "purple", tail_color= "purple")
cosmo.addPlanet(mass = m_uranus,pos = pos_uranus, speed = vel_uranus, color = "cyan", tail_color= "cyan")
cosmo.addPlanet(mass = m_neptune,pos = pos_neptune, speed = vel_neptune, color = "violet", tail_color= "violet")

curr_frame = d_jupiter *1.01
cosmo.record(title = "Solar_System_narrow",
             fps = 60, xlimit = [-curr_frame, curr_frame],ylimit = [-curr_frame, curr_frame],time = 60*20, dt = 10)

0.........10.........20.........30.........40.........50.........60.........70.........80.........90.........100.........110.........120.........130.........140.........150.........160.........170.........180.........190.........200.........210.........220.........230.........240.........250.........260.........270.........280.........290.........300.........310.........320.........330.........340.........350.........360.........370.........380.........390.........400.........410.........420.........430.........440.........450.........460.........470.........480.........490.........500.........510.........520.........530.........540.........550.........560.........570.........580.........590.........600.........610.........620.........630.........640.........650.........660.........670.........680.........690.........700.........710.........720.........730.........740.........750.........760.........770.........780.........790.........800.........810.........820.........830.........840

In [3]:
million_kilo = 1000000

m_mercury = 3.285 * 10**23
d_mercury = 57 * million_kilo
pos_mercury = np.array([0,-1]) * d_mercury
v_mercury = 1470000
vel_mercury = np.array([1,0]) * v_mercury

m_venus = 4.867 * 10**24
d_venus = 108 * million_kilo
pos_venus = np.array([0,-1]) * d_venus
v_venus = 1090000
vel_venus = np.array([1,0]) * v_venus

m_earth = 5.972 * 10**24
d_earth = 149 * million_kilo
pos_earth = np.array([0,-1]) * d_earth
v_earth = 940000
vel_earth = np.array([1,0]) * v_earth

m_mars = 6.39 * 10**23
d_mars = 228 * million_kilo
pos_mars = np.array([0,-1]) * d_mars
v_mars = 760000
vel_mars = np.array([1,0]) * v_mars

m_jupiter = 1.898 * 10**27
d_jupiter = 780 * million_kilo
pos_jupiter = np.array([0,-1]) * d_jupiter
v_jupiter = 407000
vel_jupiter = np.array([1,0]) * v_jupiter

m_saturn = 5.68 * 10**26
d_saturn = 1437 * million_kilo
pos_saturn = np.array([0,-1]) * d_saturn
v_saturn = 303300
vel_saturn = np.array([1,0]) * v_saturn

m_uranus = 8.68 * 10**25
d_uranus = 2871 * million_kilo
pos_uranus = np.array([0,-1]) * d_uranus
v_uranus = 213300
vel_uranus = np.array([1,0]) * v_uranus

m_neptune = 1.024* 10**26
d_neptune = 4530 * million_kilo
pos_neptune = np.array([0,-1]) * d_neptune
v_neptune = 170140
vel_neptune = np.array([1,0]) * v_neptune

m_sun = 1.989 * 10**30
# Gliese 876
m_gliese_sun = 0.37*2*10**30
m_planetd = 6.83 * m_earth
m_planetc = 0.7142 * m_jupiter
m_planetb = 2.2756 * m_jupiter
m_planeta = 14.6 * m_earth

d_planetd = 0.02 * d_earth 
d_planetc = 0.129 * d_earth
d_planetb = 0.208 * d_earth
d_planeta = 0.33 * d_earth

pos_planet_d = np.array([0,-1]) * d_planetd
pos_planet_c = np.array([0,1]) * d_planetc
pos_planet_b = np.array([0,1]) * d_planetb
pos_planet_a = np.array([0,-1]) * d_planeta

vel_planetd = np.array([1,0]) * v_earth * 3.5
vel_planetc = np.array([-1,0]) * v_earth * 1.5
vel_planetb = np.array([-1,0]) * v_earth * 1.3
vel_planeta = np.array([1,0]) * v_earth * 1.05

e_move = np.array([-700000, 0])

cosmo = CosmicSimulation(planet_destroy = False, planet_melt = False, sun_merge = True, merge_distance = 5000000,
                        tail_length = 200)

cosmo.addSun(mass= m_sun, pos = (0,0), speed= e_move, color = "yellow", tail_color= "yellow")
cosmo.addPlanet(mass = m_mercury,pos = pos_mercury, speed = vel_mercury + e_move, color = "orange", tail_color= "orange")
cosmo.addPlanet(mass = m_venus,pos = pos_venus, speed = vel_venus + e_move, color = "blue", tail_color= "blue")
cosmo.addPlanet(mass = m_earth,pos = pos_earth, speed = vel_earth + e_move, color = "green", tail_color= "green")
cosmo.addPlanet(mass = m_mars,pos = pos_mars, speed = vel_mars + e_move, color = "red", tail_color= "red")
cosmo.addPlanet(mass = m_jupiter,pos = pos_jupiter, speed = vel_jupiter + e_move, color = "brown", tail_color= "brown")
cosmo.addPlanet(mass = m_saturn,pos = pos_saturn, speed = vel_saturn + e_move, color = "purple", tail_color= "purple")
cosmo.addPlanet(mass = m_uranus,pos = pos_uranus, speed = vel_uranus + e_move, color = "cyan", tail_color= "cyan")
cosmo.addPlanet(mass = m_neptune,pos = pos_neptune, speed = vel_neptune+e_move, color = "violet", tail_color= "violet")


curr_frame = d_jupiter *1.01
cosmo.record(title = "collision attempt move",
             fps = 60, xlimit = [-curr_frame, curr_frame],ylimit = [-curr_frame, curr_frame],time = 3000, dt = 0.8)

0.........10.........20.........30.........40.........50.........60.........70.........80.........90.........100.........110.........120.........130.........140.........150.........160.........170.........180.........190.........200.........210.........220.........230.........240.........250.........260.........270.........280.........290.........300.........310.........320.........330.........340.........350.........360.........370.........380.........390.........400.........410.........420.........430.........440.........450.........460.........470.........480.........490.........500.........510.........520.........530.........540.........550.........560.........570.........580.........590.........600.........610.........620.........630.........640.........650.........660.........670.........680.........690.........700.........710.........720.........730.........740.........750.........760.........770.........780.........790.........800.........810.........820.........830.........840

In [4]:
cosmo = CosmicSimulation(planet_destroy = False, planet_melt = False, sun_merge = True, merge_distance = 5000000,
                        tail_length = 200)
cosmo.addSun(mass= m_sun +m_gliese_sun , pos = (100,100), color = "yellow", tail_color= "yellow")
for i in p:
    cosmo.addPlanet(mass = i.mass, pos = i.arr[0:2], speed = i.arr[2:4],color = i.color, tail_color = i.tail_color)
cosmo.record(title = "collision_p2",
             fps = 60, xlimit = [-curr_frame, curr_frame],ylimit = [-curr_frame, curr_frame],time = 140, dt = 0.8)

IndexError: index 0 is out of bounds for axis 0 with size 0

In [59]:
cosmo = CosmicSimulation(planet_destroy = False, G=1,planet_melt = False, sun_merge = True, merge_distance = 1000,
                        tail_length = 1, p=p)

cosmo.addSun(mass= 1, pos = (10,0), speed = [0,0],color = "yellow", tail_color= "yellow")
cosmo.addSun(mass= 1, pos = (-10,0), speed = [0,0], color = "red", tail_color= "red")
cosmo.addPlanet(mass = 1,pos = (0,10), speed = [0,0], color = "black", tail_color= "black")

cosmo.record(title = "collision part 2",
             fps = 60,time = 100, xlimit =[-5, 5], ylimit =[-5, 5], dt = 0.1)

0Sun 0 has absorbed Sun 1
.........10.........20.........30.........40.........50.........60.........

KeyboardInterrupt: 